## Objective:
We will create a model to detect Fake news using Python.
Fake news refers to information content that is false, misleading or whose source cannot be verified.

In [58]:
import numpy as np
import pandas as pd
import re
import string
import itertools
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import PassiveAggressiveClassifier
from sklearn.metrics import accuracy_score, confusion_matrix

In [15]:
data = pd.read_csv('fakenews.csv')
data.head()

id                                              title              author   
0   0  House Dem Aide: We Didn’t Even See Comey’s Let...       Darrell Lucus  \
1   1  FLYNN: Hillary Clinton, Big Woman on Campus - ...     Daniel J. Flynn   
2   2                  Why the Truth Might Get You Fired  Consortiumnews.com   
3   3  15 Civilians Killed In Single US Airstrike Hav...     Jessica Purkiss   
4   4  Iranian woman jailed for fictional unpublished...      Howard Portnoy   

                                                text  label  
0  House Dem Aide: We Didn’t Even See Comey’s Let...      1  
1  Ever get the feeling your life circles the rou...      0  
2  Why the Truth Might Get You Fired October 29, ...      1  
3  Videos 15 Civilians Killed In Single US Airstr...      1  
4  Print \nAn Iranian woman has been sentenced to...      1

## Data Preprocessing

In [16]:
#Check shape of data so that we can decide if we can drop rows with missing values without affecting the data
data.shape

(20800, 5)

In [17]:
#check missing values
data.isnull().sum()

id           0
title      558
author    1957
text        39
label        0
dtype: int64

Since there are 1957 rows with missing values, hence we may need to delete these many rows, but it won't be ideal as we may lose almost 10% data. Hence we will fill cells with missing values with empty string

In [18]:
#Fill missing values and assign to new variable to avoid overwriting original datsaet
df = data.fillna('')
df.isnull().sum()

id        0
title     0
author    0
text      0
label     0
dtype: int64

Now we can check if we can remove any columns that are not required, i.e., columns that does not determine if the news is fake or not

We can combine **title** and **author** columns and make one column named **content**

We can drop columns **title** and **author**

In [19]:
df['content'] = df['author'] + ' ' + df['title']
df = df.drop(['author', 'title'], axis = 1)
df.head()

id                                               text  label   
0   0  House Dem Aide: We Didn’t Even See Comey’s Let...      1  \
1   1  Ever get the feeling your life circles the rou...      0   
2   2  Why the Truth Might Get You Fired October 29, ...      1   
3   3  Videos 15 Civilians Killed In Single US Airstr...      1   
4   4  Print \nAn Iranian woman has been sentenced to...      1   

                                             content  
0  Darrell Lucus House Dem Aide: We Didn’t Even S...  
1  Daniel J. Flynn FLYNN: Hillary Clinton, Big Wo...  
2  Consortiumnews.com Why the Truth Might Get You...  
3  Jessica Purkiss 15 Civilians Killed In Single ...  
4  Howard Portnoy Iranian woman jailed for fictio...

**Stemming**

Stemming is a natural language processing technique that is used to reduce words to their base form, also known as the root form. The process of stemming is used to normalize text and make it easier to process. It is an important step in text pre-processing, and it is commonly used in information retrieval and text mining applications.

A stemming algorithm reduces the words “chocolates”, “chocolatey”, “choco” to the root word, “chocolate” and “retrieval”, “retrieved”, “retrieves” reduce to the stem “retrieve”.

There are several different algorithms for stemming. The Porter stemmer is the most widely used algorithm.

In [20]:
import nltk
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer

In [21]:
stemmer = PorterStemmer()

In [22]:
#Example
sentence = "Programmers program with programming languages"
stemmer.stem(sentence)

'programmers program with programming languag'

We create a new Porter stemmer for us so that we can use the function without explicitly typing PorterStemmer() every time.

In [26]:
for i in range(0,len(df)):
    sentence = re.sub('[^a-zA-Z]', ' ', df['content'][i]) #1
    sentence = sentence.lower().split() #2 #3
    sentence = [stemmer.stem(word) for word in sentence if word not in stopwords.words('english')] #4
    sentence = ' '.join(sentence) #5
    df['content'][i] = sentence

C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\A

C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\A

C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\A

C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\A

C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\A

...

C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\A

C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\A

C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\A

C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\A

C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\AppData\Local\Temp\ipykernel_20552\1089516598.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['content'][i] = sentence
C:\Users\parij\A

**#1.** Replace all nonalphabetical values with space, i.e. remove all that is not a letter

**#2.** Convert all letter to lowercase for convenience

**#3.** Split each sentence into a list of words

**#4.** Use stemmer and stem each word in the list. Stopwords are the English words which does not add much meaning to a sentence. They can safely be ignored without sacrificing the meaning of the sentence. For example, the words like the, he, have etc.

**#5.** Join all stemmed content to form a sentence again

**#6.** Now append the stemmed sentence to list

In [27]:
df.head()

id                                               text  label   
0   0  House Dem Aide: We Didn’t Even See Comey’s Let...      1  \
1   1  Ever get the feeling your life circles the rou...      0   
2   2  Why the Truth Might Get You Fired October 29, ...      1   
3   3  Videos 15 Civilians Killed In Single US Airstr...      1   
4   4  Print \nAn Iranian woman has been sentenced to...      1   

                                             content  
0  darrel lucu hous dem aid even see comey letter...  
1  daniel j flynn flynn hillari clinton big woman...  
2             consortiumnew com truth might get fire  
3  jessica purkiss civilian kill singl us airstri...  
4  howard portnoy iranian woman jail fiction unpu...

We now count how many times a word appears, given that the headline is of news, and adds one count to its entry into the dictionary that counts how many times each word appears.

In [49]:
def extract_words(data):
    dictionary = {}
    for sentence in data['content']:
        words = sentence.split()
        for word in words:
            if word not in dictionary:
                dictionary[word] = 1
            else:
                dictionary[word] += 1
    return dictionary

In [50]:
real_words = extract_words(df[:][df['label']==0])
fake_words = extract_words(df[:][df['label']==1])

Create a function to count total number of words in all fake news headlines, or real news headlines.

In [51]:
def count_total(dictionary):
    length = 0
    for word in dictionary:
        length += dictionary[word]
    return length

In [52]:
real_count = count_total(real_words)
fake_count = count_total(fake_words)

Create a function that changes the number into a probability, by calculating the total number of words for fake news headlines, or real news headlines.

In [53]:
def count_prob(dictionary, length):
    for word in dictionary:
        dictionary[word] = dictionary[word]/length
    return dictionary

In [54]:
real_prob = count_prob(real_words, real_count)
fake_prob = count_prob(fake_words, fake_count)

Now, create a function that multiplies the relevant probabilites, to compute a “score” for the headline.

In [73]:
def calculate_probability(dictionary, data, initial_prob):
    data.translate(str.maketrans('', '', string.punctuation))
    words = data.lower().split()
    probability = initial_prob
    for word in words:
        if word in dictionary:
            probability *= dictionary[word]
            print(word, dictionary[word])
    return probability

In [80]:
X = df.content.values
y = df.label.values

In [81]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, stratify = y, random_state = 2)

In [77]:
X = 'Hillary Clinton eats Donald Trump'
calculate_probability(fake_prob,X,1) > calculate_probability(real_prob,X,1)

hillary 2.168256721595837e-05
clinton 0.010613616652211623
donald 0.002883781439722463
trump 0.015893321769297485
clinton 0.002336187788036805
donald 0.005094962445581974
trump 0.01813136870305698


False